# Correction terms on $B_0,B_1,B_2,B_3$

The code performs the computation of the intersection numbers at every center of our sequence of five blow-ups and the Chern classes of the vector bundles with are relevant for attaining the characteristic numbers we are interested in.
The code follows the notation of the article: the center of each blow-up is denoted by $B_i$, while the blow-ups are called $V_i$. Hence $V_{i+1}$ denotes the blow-up of $V_{i}$ at the center $B_i$ and $\pi_{i+1}:V_{i+1}\to V_i$ the corresponding blow-up map, for $i=0,\dots,4$. For $i\leq3$, $S_i$ indicates the proper transform in $V_i$ of the locus $S_0$ of non reduced cubics. 

The part of the code computing the intersection numbers for the certers $B_1,B_2,B_3$ works for any value of $n$. The last part of the code starting from the computation of the Chern class of the vector bundle $\mathcal{E}$ requires $n\leq 3$ instead. The reason for this are made more precise below.

In [1]:
n = 3

Running the code for $n=4,5$ it is possible to verify what stated in Remark 4.15. Uncomment the next code lines if you want to check that out.

In [2]:
#n = 4
#n = 5
#conjecture=false

In the next lines each ```di``` denotes the rank of the normal bundle $N_{B_{i-1}}V_{i-1}$

In [3]:
Q = binomial(n+2, 2)
C = binomial(n+3, 3)
d1 = C-1 - n
d2 = C-1 - Q + 2
d3 = 2
#dimensions of the centers Bi
dimB0 = n
dimB1 = Q-2
dimB2 = C-3
dimB3 = 2*n
dimB4=2*n+n*(n-1)/2-1
print(dimB0,dimB1,dimB2,dimB3,dimB4)

(3, 8, 17, 6, 8)


We define a ring quotient ```CHB2``` which carries informations about the relations holding among the generators of the Chow ring of $B_2$ (hence also of $B_0$ and $B_1$). This is described in Subsection 3.2.

In [4]:
h,eps,phi = var('h,eps,phi')
R = QQ[h,eps,phi]
relations2 = []
relations2.append(h**(n+1))
relations2.append(eps**(dimB1+1))
relations2.append(phi**(dimB2+1))
for u in range(n+1):
    for v in range(dimB1+1):
            if u+v>=(dimB1+1):
                relations2.append(h**u*eps**v)
for u in range(n+1):
    for v in range(dimB1+1):
        for o in range(dimB2+1):
            if u+v+o>=(dimB2+1):
                relations2.append(h**u*eps**v*phi**o)               
# J is the ideal generated by the relations holding between h, eps, phi
J = R.ideal(relations2)    
CHB2.<h,eps,phi> = R.quotient(J)
L2 = CHB2.lifting_map()

## Correction term on $B_0$ and intersection numbers on $B_1$

With the name $\textit{correction term on } B_i$ we refer to

$$\int_{B_i}\frac{(B_i\circ P_i)^{n_p}(B_i\circ L_i)^{n_{\ell}}}{c(N_{B_i}V_i)},\qquad \quad \hbox{for } i = 0,\dots,4$$
    
appearing in Lemma 4.1. This is denoted in the code by ```corri``` for $i=0,\dots,4$.

Let's compute the Segre class $s(\hbox{num}\,c(N_{B_0}V_0))$, we recover it iteratively by knowing the numerator of the Chern class.

In [5]:
cNB0V0_num=(1+3*h)**C
sNB0V0_num=1
cNB0V0_num_pol=L2(cNB0V0_num)
for deg in range(dimB1):
    product=sNB0V0_num*(cNB0V0_num)
    product_pol=L2(product)
    s_deg=0
    for h_exp in range(n+1):
        if h_exp==deg+1:
            s_deg=s_deg+product_pol.coefficient([h_exp,0,0])*h^(h_exp)
    sNB0V0_num=sNB0V0_num-s_deg
print(sNB0V0_num)
cNB0V0_num*sNB0V0_num == 1

-41580*h^3 + 1890*h^2 - 60*h + 1


True

In [6]:
corr0=zero_matrix(C,1)

for n_points in range(C):
    n_lines=C-1-n_points
    integral0=((3*h)**n_points*(2+12*h)**n_lines*(1+h)**(n+1))*sNB0V0_num
    integral0_pol=L2(integral0)
    deg1=integral0_pol.degree(std_grading=True)
    if deg1==dimB0 :
        corr0[n_points,0]=integral0_pol.lc()
print(corr0)

[9948889088]
[ 877658112]
[  54263808]
[   1769472]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]


Now we can compute the $\color{blue}{\text{intersection numbers on $B_1$}}$ following the strategy explicited in the article.

In [7]:
cB1_num=(1+2*h)**Q
sB1_num=1
cB1_num_pol=L2(cB1_num)
for deg in range(dimB0):
    product=sB1_num*(cB1_num)
    product_pol=L2(product)
    s_deg=0
    for h_exp in range(n+1):
        if h_exp==deg+1:
            s_deg=s_deg+product_pol.coefficient([h_exp,0,0])*h^(h_exp)
    sB1_num=sB1_num-s_deg
print(sB1_num)
sB1_num*cB1_num == 1

-1760*h^3 + 220*h^2 - 20*h + 1


True

We compute the coefficients $a_i$ as explained in Subsection 3.1. The output matrix gives the intersection numbers on $B_1$ which are explicited in Table 1. The entry $(i)$ of $i_1$ contains the intersection number for $h^i\epsilon^{\dim(B_1)-i}$.  

In [8]:
#This is the segre class of the bundle associated to B1
sB1=(1+h)**(n+1)*sB1_num
print(sB1)
sB1_pol=L2(sB1)

#We present here the sequence a_rec that can be obtained recursevely
a_rec = matrix(1,n+1)
for u in range(n+1):
    a_rec[0,u]=sB1_pol.coefficient([u,0,0])

#i1 is the vector of the intersection numbers
i1 = matrix(1, n+1)
for u in range(n+1):
    i1[0,u]=(-1)^(Q-u)*a_rec[0,n-u]
print(i1)

-996*h^3 + 146*h^2 - 16*h + 1
[-996 -146  -16   -1]


## Correction term on $B_1$ and intersection numbers on $B_2$

Computing the Segre class $s(\text{num}\,c(N_{B_1}V_1))$, we recover it iteratively by knowing the Chern class $c(N_{B_1}V_1)$

In [9]:
#Define a function iteratively yourself
cNB1V1_num=(1+eps)*(1+3*h-eps)**C
sNB1V1_num=1
cNB1V1_num_pol=L2(cNB1V1_num)
for deg in range(dimB1):
    product=sNB1V1_num*(cNB1V1_num)
    product_pol=L2(product)
    s_deg=0
    for h_exp in range(n+1):
        for eps_exp in range(dimB1+1):
            if (h_exp+eps_exp)==deg+1:
                s_deg=s_deg+product_pol.coefficient([h_exp,eps_exp,0])*h^(h_exp)*eps^(eps_exp)
    sNB1V1_num=sNB1V1_num-s_deg
print(sNB1V1_num)
sNB1V1_num*cNB1V1_num == 1

-2820205080*h^3*eps^5 + 455656320*h^2*eps^6 - 42111840*h*eps^7 + 1704377*eps^8 - 536548320*h^3*eps^4 + 103802580*h^2*eps^5 - 11169960*h*eps^6 + 515698*eps^7 - 85072680*h^3*eps^3 + 20521620*h^2*eps^4 - 2643840*h*eps^5 + 142102*eps^6 - 10561320*h^3*eps^2 + 3386880*h^2*eps^3 - 543960*h*eps^4 + 34998*eps^5 - 914760*h^3*eps + 438480*h^2*eps^2 - 93600*h*eps^3 + 7506*eps^4 - 41580*h^3 + 39690*h^2*eps - 12660*h*eps^2 + 1349*eps^3 + 1890*h^2 - 1200*h*eps + 191*eps^2 - 60*h + 19*eps + 1


True

In [10]:
corr1=zero_matrix(C,1)

for n_points in range(19):
    n_lines=C-1-n_points
    integral1=((3*h)**n_points*(1+12*h-2*eps)**n_lines*(1+2*h-eps)**Q)*sNB1V1_num
    integral1_pol=L2(integral1)
    deg2=integral1_pol.degree(std_grading=True)
    if deg2==dimB1 :
        for h_exp in range(n+1):
            for eps_exp in range(dimB1+1):
                if (h_exp+eps_exp)==deg2:
                    corr1[n_points,0]=corr1[n_points,0]+integral1_pol.coefficient([h_exp,eps_exp,0])*i1[0,h_exp]
print(corr1)

[2199770536]
[ 203305944]
[  13011156]
[    434889]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]


We can compute the $\color{blue}{\text{intersection numbers on $B_2$}}$.

Here the code returns the Segre class $s(\text{num}\,c(N_{B_1}E_1))$.

In [11]:
cB2_num=(1+3*h-eps)^C
sB2_num=1
cB2_num_pol=L2(cB2_num)
for deg in range(dimB1):
    product=sB2_num*(cB2_num)
    product_pol=L2(product)
    s_deg=0
    for h_exp in range(n+1):
        for eps_exp in range(dimB1+1):
            if (h_exp+eps_exp)==deg+1:
                s_deg=s_deg+product_pol.coefficient([h_exp,eps_exp,0])*h^(h_exp)*eps**(eps_exp)
    sB2_num=sB2_num-s_deg
(1+3*h-eps)^C*sB2_num == 1   

True

Here we compute the coefficients $c_{j,k}$ of Subsection 3.2 which then give us the intersection number on $B_2$. The ones for $n=3$ are displayed in Table 2 in our article.

The entry $(i,j)$ of $i_2$ contains the intersection number for $h^i\epsilon^j\phi^{dimB2-i-j}$.

In [12]:
#computing the c_ij and then intersection numbers
sB2=(1+2*h-eps)**Q*sB2_num
print(sB2)
sB2_pol=L2(sB2)

c = matrix(dimB0+1, dimB1+1)
for u in range(n+1):
    for v in range(dimB1+1):
        c[u,v]=sB2_pol.coefficient([u,v,0])

i2 = matrix(dimB0+1, dimB1+1)
for u in range(n+1):
    for v in range(dimB1+1):
        if u+v<=dimB1:
            for a in range(min(n+1-u,Q-1-u-v)):
                i2[u,v]=i2[u,v]+c[a,dimB1-u-v-a]*i1[0,a+u]
            i2[u,v]=(-1)^(C-1-u-v)*i2[u,v]
        
print(i2)

-84280560*h^3*eps^5 + 10767120*h^2*eps^6 - 777920*h*eps^7 + 24310*eps^8 - 24788400*h^3*eps^4 + 3800160*h^2*eps^5 - 320320*h*eps^6 + 11440*eps^7 - 6197100*h^3*eps^3 + 1187550*h^2*eps^4 - 120120*h*eps^5 + 5005*eps^6 - 1239420*h^3*eps^2 + 316680*h^2*eps^3 - 40040*h*eps^4 + 2002*eps^5 - 177060*h^3*eps + 67860*h^2*eps^2 - 11440*h*eps^3 + 715*eps^4 - 13620*h^3 + 10440*h^2*eps - 2640*h*eps^2 + 220*eps^3 + 870*h^2 - 440*h*eps + 55*eps^2 - 40*h + 10*eps + 1
[-1370200  -641680   251160    24388   -49400    12900     4460    -4120      996]
[ -345280    -3640    31668   -10790     -320     1860     -820      146        0]
[  -40040     8008        0     -880      440     -120       16        0        0]
[   -2002      715     -220       55      -10        1        0        0        0]


## Correction term on $B_2$ and intersection numbers on $B_3$

Computing the Segre class $s(N_{B_2}V_2)$

In [13]:
cNB2V2=((1+phi)*(1+eps-phi))
sNB2V2=1
cNB1V1_pol=L2(cNB2V2)
for deg in range(dimB2):
    product=sNB2V2*(cNB2V2)
    product_pol=L2(product)
    s_deg=0
    for h_exp in range(n+1):
        for eps_exp in range(dimB1+1):
            for phi_exp in range(dimB2+1):
                if (h_exp+eps_exp+phi_exp)==deg+1:
                    s_deg=s_deg+product_pol.coefficient([h_exp,eps_exp,phi_exp])*h^(h_exp)*eps^(eps_exp)*phi^(phi_exp)
    sNB2V2=sNB2V2-s_deg
#print(sNB2V2)    
sNB2V2*cNB2V2 == 1

True

In [14]:
corr2=zero_matrix(C,1)

for n_points in range(C):
    n_lines=C-1-n_points
    integral2=((3*h)**n_points*(1+12*h-2*eps-phi)**n_lines)*sNB2V2
    integral2_pol=L2(integral2)
    deg3=integral2_pol.degree(std_grading=True)
    if deg3==dimB2 :
        for h_exp in range(n+1):
            for eps_exp in range(dimB1+1):
                for phi_exp in range(dimB2+1):
                    if (h_exp+eps_exp+phi_exp)==deg3:
                        corr2[n_points,0]=corr2[n_points,0]+integral2_pol.coefficient([h_exp,eps_exp,phi_exp])*i2[h_exp,eps_exp]
print(corr2)

[49885157976]
[ 5677810728]
[  443328300]
[   17951031]
[          0]
[          0]
[          0]
[          0]
[          0]
[          0]
[          0]
[          0]
[          0]
[          0]
[          0]
[          0]
[          0]
[          0]
[          0]
[          0]


Then we construct the ring ```CHB3``` which gives information about the Chow ring of $B_3$, described in Subsection 3.3. The additional relation is coming from $\Delta+\sum_{i=1}^{n}(-1)^n\cdot e^{i}m^{n-i} \binom{n+1}{n-i}$. 

In [15]:
l,m,e = var('l, m, e')
S = QQ[l, m, e]
relations3 = []
relations3.append(m**(n+1))
relations3.append(l**(n+1))
relations3.append(e**(2*n+1))
for u in range(n+1,2*n+1):
    for o in range(2*n+1-u,n+1):
        if u != 0:
            relations3.append((e**u)*(m**o))
for u in range(n+1):
    if u != 0:
        relations3.append(e*(m**u-l**u)) 
        
print(relations3)
# I is the ideal generated by the relations holding between l, m, e
I = S.ideal(relations3)
CHB3.<l,m,e> = S.quotient(I)
L3 = CHB3.lifting_map()

[m^4, l^4, e^7, e^4*m^3, e^5*m^2, e^5*m^3, e^6*m, e^6*m^2, e^6*m^3, -e*(l - m), -(l^2 - m^2)*e, -(l^3 - m^3)*e]


We can compute the $\color{blue}{\text{intersection numbers on $B_3$}}$.

Here the code returns the numerator of the Segre class $s(N_{e}B_3)$

In [16]:
cNeB3=(1+h)**(n+1)
sNeB3=1
cNeB3_pol=L2(cNeB3)
for deg in range(dimB0):
    product=sNeB3*(cNeB3)
    product_pol=L2(product)
    s_deg=0
    for h_exp in range(n+1):
        if h_exp==deg+1:
            s_deg=s_deg+product_pol.coefficient([h_exp,0,0])*h^(h_exp)
    sNeB3=sNeB3-s_deg
sNeB3*cNeB3 == 1

True

Here we compute the coefficients $d_{j,k}$ of Subsection 3.3 which then give us the intersection number on $B_3$. The ones for $n=3$ are displayed in Table 3 in our article.

The entry $(i)$ of $i_3$ contains the intersection number for $m^i e^{\dim(B_3)-i}$

In [17]:
print(sNeB3)
sNeB3_pol=L2(sNeB3)

d = matrix(1, n+1)
for u in range(n+1):
    d[0,u]=sNeB3_pol.coefficient([u,0,0])

i3 = matrix(1, n+1)
for u in range(n+1):
    i3[0,u]=(-1)^(2*n-u-1)*d[0,n-u]
print(i3)


-20*h^3 + 10*h^2 - 4*h + 1
[20 10  4  1]


# Computing the Chern class $c(N_{B_3}{V_3})$

The goal of this section of the code is to compute the Chern class $c(N_{B_3}{V_3})$. The results for $n=3,4$ are the polynomial illustrated in the Subsection 3.3. One can check that running the code for $n=2$ the output is precisely the Chern class as in Theorem III (5) in Aluffi's work, [Alu90].
The strategy to get such Chern class is to apply multiple times [Ful16, Theorem 15.4] as explained in the proof in Subsection 3.3.

In [18]:
a = matrix(1, n+1);
for s in range(n+1):
        a[0, s] = binomial(n+1, s)
a

[1 4 6 4]

Here we compute the coefficients of the expansion of the polynomial given by the Chern class $c(N_{B_0}V_0)$. This is computed in Subsection 3.0.

In [19]:
cNB0V0=cNB0V0_num*sNeB3
print(cNB0V0)
cNB0V0_pol=L2(cNB0V0)

coeff_cNB0V0= matrix(1, n+1)
for u in range(n+1):
    coeff_cNB0V0[0,u]=cNB0V0_pol.coefficient([u,0,0])
print(coeff_cNB0V0)

24520*h^3 + 1480*h^2 + 56*h + 1
[    1    56  1480 24520]


Computing Segre $s($den $c(N_{B_1}E_1))$ of the denominator of $c(N_{B_1}E_1)$.

In [20]:
cNB1V1_den=(1+2*h-eps)^Q
sNB1V1_den=1
cNB1V1_den_pol=L2(cNB1V1_den)
for deg in range(dimB1):
    product=sNB1V1_den*(cNB1V1_den)
    product_pol=L2(product)
    s_deg=0
    for h_exp in range(n+1):
        for eps_exp in range(dimB1+1):
            if (h_exp+eps_exp)==deg+1:
                s_deg=s_deg+product_pol.coefficient([h_exp,eps_exp,0])*h^(h_exp)*eps**(eps_exp)
    sNB1V1_den=sNB1V1_den-s_deg
cNB1V1_den*sNB1V1_den == 1

True

In [21]:
cNB1V1=cNB1V1_num*sNB1V1_den
print(cNB1V1)
cNB1V1_pol=L2(cNB1V1)

coeff_cNB1V1 = matrix(n+1, dimB1+1)
for u in range(n+1):
    for v in range (dimB1+1):
        if u + v <= dimB1:
            coeff_cNB1V1[u,v]=cNB1V1_pol.coefficient([u,v,0])
print(coeff_cNB1V1)

112280*h^3*eps^5 - 20440*h^2*eps^6 + 1920*h*eps^7 - 75*eps^8 + 10220*h^2*eps^5 - 1680*h*eps^6 + 90*eps^7 - 112280*h^3*eps^3 + 10220*h^2*eps^4 - 42*eps^6 + 112280*h^3*eps^2 - 20440*h^2*eps^3 + 1680*h*eps^4 - 42*eps^5 - 48120*h^3*eps + 14600*h^2*eps^2 - 1920*h*eps^3 + 90*eps^4 + 8020*h^3 - 5110*h^2*eps + 1080*h*eps^2 - 75*eps^3 + 730*h^2 - 320*h*eps + 35*eps^2 + 40*h - 9*eps + 1
[      1      -9      35     -75      90     -42     -42      90     -75]
[     40    -320    1080   -1920    1680       0   -1680    1920       0]
[    730   -5110   14600  -20440   10220   10220  -20440       0       0]
[   8020  -48120  112280 -112280       0  112280       0       0       0]


Here we compute the coefficients of the expansion of the polynomial given by the Chern class $c(N_{B_2}V_2)$. This is computed in Subsection 3.2.

In [22]:
coeff_cNB2V2 = matrix(dimB1+1,dimB2+1)
coeff_cNB2V2[0,0] = 1; coeff_cNB2V2[1,0] = 1; coeff_cNB2V2[1,1] = 1; coeff_cNB2V2[0,2] = -1
print(coeff_cNB2V2)

[ 1  0 -1  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0]
[ 1  1  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0]
[ 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0]
[ 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0]
[ 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0]
[ 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0]
[ 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0]
[ 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0]
[ 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0]


Now we can compute the pullback of $TV_1$ and $TV_2$

In [23]:
pbcTV1=(1+3*h)**C
for j in range(d1+1):
    if j<=n:
        temp=0
        for o in range(d1-j):
            temp=temp+ binomial(d1-j, o+1)*(-eps)**o
        pbcTV1=pbcTV1+((1-eps)**(d1-j)-temp)*eps*(h**j)*(1+h)**(n+1)*coeff_cNB0V0[0,j] 

cTB1_pol=L2(pbcTV1*sNB1V1_num*(1+2*h-eps)**Q)
print("c(TB1)=",cTB1_pol)

coeff_cTB1= matrix(n+1, dimB1+1)
for u in range(n+1):
    for v in range (dimB1+1):
        if u + v <= dimB1:
            coeff_cTB1[u,v]=cTB1_pol.coefficient([u,v,0])
print(coeff_cTB1)

('c(TB1)=', -120*h^3*eps^5 + 6*h^2*eps^6 + 980*h^3*eps^4 - 100*h^2*eps^5 + 4*h*eps^6 - 3220*h^3*eps^3 + 520*h^2*eps^4 - 40*h*eps^5 + eps^6 + 4920*h^3*eps^2 - 1200*h^2*eps^3 + 140*h*eps^4 - 6*eps^5 - 3524*h^3*eps + 1390*h^2*eps^2 - 240*h*eps^3 + 15*eps^4 + 960*h^3 - 796*h^2*eps + 220*h*eps^2 - 20*eps^3 + 180*h^2 - 104*h*eps + 15*eps^2 + 20*h - 6*eps + 1)
[    1    -6    15   -20    15    -6     1     0     0]
[   20  -104   220  -240   140   -40     4     0     0]
[  180  -796  1390 -1200   520  -100     6     0     0]
[  960 -3524  4920 -3220   980  -120     0     0     0]


In [24]:
pbcTV2=pbcTV1
for j in range(d2+1):
        temp=0
        temp2=0
        for o in range(d2-j):
            temp=temp+ binomial(d2-j, o+1)*(-phi)**o
        for i in range(j+1):
            if i<=n:
                if j<=dimB1+i:
                    temp2=temp2+coeff_cNB1V1[i,j-i]*h**i*(eps)**(j-i)
        pbcTV2=pbcTV2+((1-phi)**(d2-j)-temp)*phi*(pbcTV1*sNB1V1_num*(1+2*h-eps)**Q)*temp2 

cTB2=L2(pbcTV2*sNB2V2)

coeff_cTB2 = []
for u in range(dimB2+1):
    coeff_cTB2.append(matrix(dimB0+1, dimB1+1))
for o in range (dimB2+1):
    for u in range(n+1):
        for v in range (dimB1+1):
            if u + v + o <= dimB2: 
                if u+v<=dimB1:
                    coeff_cTB2[o][u,v]=cTB2.coefficient([u,v,o])

Then we compute the Chern classes $c(TB_1)$, $c(TB_2)$, and $c(TB_3)$.

In [25]:
cTB1=0
for i in range(dimB0+1):
    for j in range(dimB1+1):
            if i+j<=dimB1:
                cTB1=cTB1+coeff_cTB1[i,j]*m**i*(2*e)**j
print(cTB1)    

-25760*m^3*e^3 + 8320*m^2*e^4 - 1280*m*e^5 + 64*e^6 + 19680*m^3*e^2 - 9600*m^2*e^3 + 2240*m*e^4 - 192*e^5 - 7048*m^3*e + 5560*m^2*e^2 - 1920*m*e^3 + 240*e^4 + 960*m^3 - 1592*m^2*e + 880*m*e^2 - 160*e^3 + 180*m^2 - 208*m*e + 60*e^2 + 20*m - 12*e + 1


In [26]:
cTB2=0
for i in range(dimB0+1):
    for j in range(dimB1+1):
        for o in range(dimB2+1):
            if i + j + o <= dimB2: 
                if i+j<=dimB1:
                    cTB2=cTB2+coeff_cTB2[o][i,j]*m**i*(2*e)**j*e**o
print(cTB2)   

-164246460*m^3*e^3 + 82770780*m^2*e^4 - 22367360*m*e^5 + 2529946*e^6 + 16878260*m^3*e^2 - 11420920*m^2*e^3 + 3887240*m*e^4 - 531948*e^5 - 1060828*m^3*e + 1083260*m^2*e^2 - 494800*m*e^3 + 85230*e^4 + 30780*m^3 - 63192*m^2*e + 43540*m*e^2 - 10060*e^3 + 1710*m^2 - 2368*m*e + 825*e^2 + 60*m - 42*e + 1


In [27]:
cTB3 =(1+l)**(n+1)*(1+m)**(n+1) + sum((sum((binomial(n-j,o)-binomial(n-j,o+1))*(-e)**o for o in range (n-j+1)))*(1+m)**(n+1)*a[0,j]*m**j*e for j in range(n+1))
print(cTB3)

16*l^3*m^3 + 32*m^3*e^3 - 6*m^2*e^4 + 24*l^3*m^2 + 24*l^2*m^3 - 48*m^3*e^2 + 28*m^2*e^3 - 4*m*e^4 + 16*l^3*m + 36*l^2*m^2 + 16*l*m^3 - 28*m^3*e - 22*m^2*e^2 + 12*m*e^3 - e^4 + 4*l^3 + 24*l^2*m + 24*l*m^2 + 4*m^3 - 28*m^2*e - 4*m*e^2 + 2*e^3 + 6*l^2 + 16*l*m + 6*m^2 - 12*m*e + 4*l + 4*m - 2*e + 1


Following the strategy explained in the article, we can now use the outputs attained so far to compute the Chern class $c(N_{B_3}V_3)$. This will be the quotient of a polynomial $P = P_1+P_2+P_3+P_4$ and the Chern class $c(TB_3)$, more explicitly we have

$$c(N_{B_3}V_3) = \frac{P_1+P_2+P_3+P_4}{c(TB_3)}$$

where each $P_i$ is explicitly computed in the code with the ingredients we computed so far.

In [28]:
P1 = (1 +(2*m+l))**C

In [29]:
P2=0
for j in range(d1+1):
    if j<=n:
        temp=0
        temp2=0
        for o in range(d1-j+1):
            temp=temp+(binomial(d1-j, o) - binomial(d1-j, o+1))*(-2*e)**o
        P2=P2+temp*(2*e)*(m**j)*(1+m)**(n+1)*coeff_cNB0V0[0,j]   

In [30]:
P3=0
for j in range(d2+1):
    temp=0
    temp2=0
    for o in range(d2-j+1):
        temp=temp+(binomial(d2-j, o) - binomial(d2-j, o+1))*(-e)**o
    for i in range(j+1):
        if i<=n:
            if j<=dimB1+i:
                temp2=temp2+coeff_cNB1V1[i,j-i]*m**i*(2*e)**(j-i)
    P3=P3+temp*cTB1*temp2*e

In [31]:
P4=0
for j in range(d3+1):
    temp=0
    temp2=0
    for o in range(d3-j+1):
        temp=temp+(binomial(d3-j, o) - binomial(d3-j, o+1))*(-e)**o
    for i in range(j+1):
        if i<=dimB1:
            if j<=dimB2+i:
                temp2=temp2+coeff_cNB2V2[i,j-i]*(2*e)**i*e**(j-i)
    P4=P4+temp*cTB2*temp2*e

In [32]:
#Numerator 
P = P1 + P2 +P3 +P4
print(P)

6201600*l^3*m^3 - 147368200*m^3*e^3 + 71349860*m^2*e^4 - 18480120*m*e^5 + 1997998*e^6 + 620160*l^3*m^2 + 1240320*l^2*m^3 + 15817432*m^3*e^2 - 10337660*m^2*e^3 + 3392440*m*e^4 - 446718*e^5 + 38760*l^3*m + 116280*l^2*m^2 + 155040*l*m^3 - 1030048*m^3*e + 1020068*m^2*e^2 - 451260*m*e^3 + 75170*e^4 + 1140*l^3 + 6840*l^2*m + 13680*l*m^2 + 9120*m^3 - 61482*m^2*e + 41172*m*e^2 - 9235*e^3 + 190*l^2 + 760*l*m + 760*m^2 - 2308*m*e + 783*e^2 + 20*l + 40*m - 41*e + 1


We compute the Segre class $s(TB_3)$.

In [33]:
sTB3=1
cTB3_pol=L3(cTB3)
for deg in range(dimB3):
    product=sTB3*(cTB3)
    product_pol=L3(product)
    s_deg=0
    for m_exp in range(n+1):
        for l_exp in range(n+1):
            for e_exp in range(2*n+1):
                if (m_exp+l_exp+e_exp)==deg+1:
                    s_deg=s_deg+product_pol.coefficient([l_exp,m_exp,e_exp])*m^(m_exp)*l^(l_exp)*e^(e_exp)
    sTB3=sTB3-s_deg
sTB3*cTB3 == 1

True

In [34]:
#Final result

cNB3V3 = P*sTB3
cTV3=P
print(cNB3V3)

1672560*l^3*m^3 - 66343820*m^3*e^3 + 36537350*m^2*e^4 - 10851224*m*e^5 + 1356403*e^6 + 209440*l^3*m^2 + 474320*l^2*m^3 + 8045100*m^3*e^2 - 5907690*m^2*e^3 + 2193180*m*e^4 - 328977*e^5 + 15960*l^3*m + 53560*l^2*m^2 + 81680*l*m^3 - 582940*m^3*e + 642110*m^2*e^2 - 317840*m*e^3 + 59595*e^4 + 560*l^3 + 3720*l^2*m + 8400*l*m^2 + 6460*m^3 - 42166*m^2*e + 31308*m*e^2 - 7827*e^3 + 120*l^2 + 536*l*m + 610*m^2 - 1880*m*e + 705*e^2 + 16*l + 36*m - 39*e + 1


The following is the result in [Alu90], for a check in the case $n=2$.

In [34]:
cAluffi = 1+7*l+17*m-16*e+126*m^2+99*l*m+21*l^2-315*e*l+105*e^2+582*l*m^2+237*l^2*m-2517*e*l^2+1611*e^2*l-358*e^3+1026*l^2*m^2+9174*e^2*l^2-3912*e^3*l+652*e^4 
print(cAluffi)

1026*l^2*m^2 + 9174*m^2*e^2 - 3912*m*e^3 + 652*e^4 + 237*l^2*m + 582*l*m^2 - 2517*m^2*e + 1611*m*e^2 - 358*e^3 + 21*l^2 + 99*l*m + 126*m^2 - 315*m*e + 105*e^2 + 7*l + 17*m - 16*e + 1


In [35]:
cNB3V3 == cAluffi

True

Here we compute the Segre class $s(N_{B_3}V_3)$

In [35]:
sNB3V3=1
cNB3V3_pol=L3(cNB3V3)
for deg in range(dimB3):
    product=sNB3V3*(cNB3V3)
    product_pol=L3(product)
    s_deg=0
    for m_exp in range(n+1):
        for l_exp in range(n+1):
            for e_exp in range(2*n+1):
                if (m_exp+l_exp+e_exp)==deg+1:
                    s_deg=s_deg+product_pol.coefficient([l_exp,m_exp,e_exp])*m^(m_exp)*l^(l_exp)*e^(e_exp)
    sNB3V3=sNB3V3-s_deg
print(sNB3V3)
sNB3V3*cNB3V3 == 1

12784496*l^3*m^3 - 596679904*m^3*e^3 + 341353632*m^2*e^4 - 103308160*m*e^5 + 12913520*e^6 - 807456*l^3*m^2 - 1802416*l^2*m^3 - 33629704*m^3*e^2 + 25652156*m^2*e^3 - 9704280*m*e^4 + 1455642*e^5 + 35496*l^3*m + 119976*l^2*m^2 + 177616*l*m^3 - 1335004*m^3*e + 1527476*m^2*e^2 - 770464*m*e^3 + 144462*e^4 - 816*l^3 - 5576*l^2*m - 12496*l*m^2 - 9196*m^3 + 64266*m^2*e - 48624*m*e^2 + 12156*e^3 + 136*l^2 + 616*l*m + 686*m^2 - 2176*m*e + 816*e^2 - 16*l - 36*m + 39*e + 1


True

## Correction Term on $B_3$

In [36]:
corr3=zero_matrix(QQ,C,1)

for n_points in range(C):
    n_lines=C-1-n_points
    integral3=(l+2*m)**n_points*(1+4*l+8*m-6*e)**n_lines*sNB3V3
    integral3_pol=L3(integral3)
    deg4=integral3_pol.degree(std_grading=True)
    if deg4==dimB3 :
        for m_exp in range(n+1):
            for l_exp in range(n+1):
                for e_exp in range(2*n+1):
                    if (m_exp+l_exp+e_exp)==deg4:
                        if e_exp==0:
                            corr3[n_points,0]=corr3[n_points,0]+integral3_pol.coefficient([l_exp,m_exp,0])*1
                        else:
                            corr3[n_points,0]=corr3[n_points,0]+integral3_pol.coefficient([l_exp,m_exp,e_exp])*i3[0,m_exp]
print(corr3)

[-337368096]
[   7701512]
[   8284040]
[   1426504]
[    130224]
[      6240]
[       160]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]


# Computing the Chern class $c(\mathcal{E})$

Recall that this part of the code just works for $\color{blue}{n\leq 3}$.


We first compute the Chern class of the vector bundle $\mathcal{E}$ outside of $e$, where $e$ denotes the pullback of the exceptional divisor of $\text{Bl}_{\Delta} \mathbb{P}^n\times \mathbb{P}^n$. Rember that in the Chow ring of $B_3\setminus e$ the term of degree 
greater than $3$ vanishes because in the Chow Ring of $B_3\setminus e$ we have $[\Delta]=0$, by the excision theorem.

In [37]:
sTPP=1
cTPP=(1+m)**(n+1)*(1+l)**(n+1)
cTPP_pol=L3(cTPP)
for deg in range(dimB3):
    product=sTPP*(cTPP)
    product_pol=L3(product)
    s_deg=0
    for m_exp in range(n+1):
        for l_exp in range(n+1):
            for e_exp in range(2*n+1):
                if (m_exp+l_exp+e_exp)==deg+1:
                    s_deg=s_deg+product_pol.coefficient([l_exp,m_exp,e_exp])*m^(m_exp)*l^(l_exp)*e^(e_exp)
    sTPP=sTPP-s_deg
sTPP*cTPP == 1

True

In [38]:
#We know that the part of c(E) not involving e will be of this form plus multiples of the diagonal class
cE_open=(1+m+l)**Q*sTPP
print(cE_open)

-20*l^3*m^2 - 20*l^2*m^3 + 20*l^3*m + 20*l^2*m^2 + 20*l*m^3 + 20*l^3 + 40*l^2*m + 40*l*m^2 + 20*m^3 + 15*l^2 + 26*l*m + 15*m^2 + 6*l + 6*m + 1


Now we encode the Chow ring of $e$ ```CHe```. The variable $r$ is representing the class of $c_1(\mathcal{O}_e(-1))$. This must be consisten with the choice of $z$ in the Chow ring of $B_4$.

In [39]:
k,r = var('k,r')
T = QQ[k,r]
relations = []
relations.append(k**(n+1))
relations.append(r**(2*n))


temp=(n+1)*k**n
for j in range(n):
    temp=temp+(-1)**(j+1)*r**(j+1)*k**(n-j-1)*binomial(n+1,n-j-1)
relations.append(temp)
print(relations)

# E is the ideal generated by the relations holding between k, r
E = T.ideal(relations)
CHe.<k,r> = T.quotient(E)
pie = CHe.cover()
Le = CHe.lifting_map()

[k^4, r^6, 4*k^3 - 6*k^2*r + 4*k*r^2 - r^3]


We have an isomorphism of $\mathcal{E}|_e$ with an explicit bundle on $e$, given by $\frac{{Sym}^2(T\mathbb{P}^n)\otimes\mathcal{O}_e(2)}{T\mathbb{P}^n\otimes \mathcal{O}_e(1) }$. 

The next lines of the code are not automatized to work for every $n$. 

In [40]:
#Remember that c(TP^n) is
(1+h)**(n+1) 

4*h^3 + 6*h^2 + 4*h + 1

##### n=2

To find the Chern class of this bundle in the Chow ring of $e$ we use the formula for the $Sym^2$ of a bundle of rank $2$. This tells us that the total Chern class is given by 
$$2c_1^2+4c_1c_2+3c_1+4c_2+1,$$
where $c_1,c_2$ are the chern classes of the starting bundle. 

In [42]:
if n==2:
    sym_bundle=2*(3*k)^2+4*(3*k)*(3*k^2)+3*(3*k)+4*(3*k^2)+1

##### n=3

To find the chern class of this bundle in the Chow ring of $e$ we use the formula for the $Sym^2$ of a bundle of rank $3$. This tells us that the total Chern class is given by 
$$1+4c_1+5c_1^2+5c_2+2c_1^3+11c_1c_2+7c_3,$$ 
where $c_1,c_2,c_3$ are the chern classes of the starting bundle. 

In [41]:
if n==3:
    sym_bundle=1+4*(4*k)+5*(4*k)**2+5*(6*k**2)+2*(4*k)**3+11*(4*k)*(6*k**2)+7*(4*k**3) 

##### n=4

To find the chern class of this bundle in the Chow ring of $e$ we use the formula for the $Sym^2$ of a bundle of rank $4$. In general this can be found using the $\verb|Singular|$ command ```LIB "chern.lib";ring r=0, (c(1..n)), ws(1 ..n);list l=c(1..n); print( chSymm2LP(n, l));```. 

In [97]:
if n==4:
    sym_bundle=1+5*(5*k)+9*(5*k)^2+6*(10*k^2)+7*(5*k)^3+20*(5*k)*(10*k^2)+8*(10*k^3)+2*(5*k)^4+22*(5*k)^2*(10*k^2)+9*(10*k^2)^2+25*(5*k)*(10*k^3)+12*(5*k^4)+8*(5*k)^3*(10*k^2)+19*(5*k)*(10*k^2)^2+27*(5*k)^2*(10*k^3)+16*(10*k^2)*(10*k^3)+36*(5*k)*(5*k^4)+10*(5*k)^2*(10*k^2)^2+4*(10*k^2)^3+10*(5*k)^3*(10*k^3)+37*(5*k)*(10*k^2)*(10*k^3)-(10*k^3)^2+39*(5*k)^2*(5*k^4)+16*(10*k^2)*(5*k^4)+4*(5*k)*(10*k^2)^3+22*(5*k)^2*(10*k^2)*(10*k^3)+8*(10*k^2)^2*(10*k^3)+6*(5*k)*(10*k^3)^2+14*(5*k)^3*(5*k^4)+48*(5*k)*(10*k^2)*(5*k^4)-32*(10*k^3)*(5*k^4)+12*(5*k)*(10*k^2)^2*(10*k^3)+8*(5*k)^2*(10*k^3)^2-4*(10*k^2)*(10*k^3)^2+28*(5*k)^2*(10*k^2)*(5*k^4)+16*(10*k^2)^2*(5*k^4)-16*(5*k)*(10*k^3)*(5*k^4)-64*(5*k^4)^2+8*(5*k)*(10*k^2)*(10*k^3)^2-8*(10*k^3)^3+16*(5*k)*(10*k^2)^2*(5*k^4)+8*(5*k)^2*(10*k^3)*(5*k^4)-64*(5*k)*(5*k^4)^2+16*(5*k)*(10*k^2)*(10*k^3)*(5*k^4)-16*(10*k^3)^2*(5*k^4)-16*(5*k)^2*(5*k^4)^2

##### n=5

In [98]:
if n==5:
    sym_bundle=1+6*(6*k)+14*(6*k)^2+7*(15*k^2)+16*(6*k)^3+31*(6*k)*(15*k^2)+9*(20*k^3)+9*(6*k)^4+51*(6*k)^2*(15*k^2)+15*(15*k^2)^2+38*(6*k)*(20*k^3)+13*(15*k^4)+2*(6*k)^5+37*(6*k)^3*(15*k^2)+48*(6*k)*(15*k^2)^2+61*(6*k)^2*(20*k^3)+30*(15*k^2)*(20*k^3)+53*(6*k)*(15*k^4)+21*(6*k^5)+10*(6*k)^4*(15*k^2)+51*(6*k)^2*(15*k^2)^2+13*(15*k^2)^3+44*(6*k)^3*(20*k^3)+98*(6*k)*(15*k^2)*(20*k^3)+7*(20*k^3)^2+84*(6*k)^2*(15*k^4)+34*(15*k^2)*(15*k^4)+84*(6*k)*(6*k^5)+18*(6*k)^3*(15*k^2)^2+27*(6*k)*(15*k^2)^3+12*(6*k)^4*(20*k^3)+108*(6*k)^2*(15*k^2)*(20*k^3)+33*(15*k^2)^2*(20*k^3)+30*(6*k)*(20*k^3)^2+60*(6*k)^3*(15*k^4)+120*(6*k)*(15*k^2)*(15*k^4)-12*(20*k^3)*(15*k^4)+132*(6*k)^2*(6*k^5)+48*(15*k^2)*(6*k^5)+14*(6*k)^2*(15*k^2)^3+4*(15*k^2)^4+40*(6*k)^3*(15*k^2)*(20*k^3)+76*(6*k)*(15*k^2)^2*(20*k^3)+41*(6*k)^2*(20*k^3)^2+11*(15*k^2)*(20*k^3)^2+16*(6*k)^4*(15*k^4)+137*(6*k)^2*(15*k^2)*(15*k^4)+41*(15*k^2)^2*(15*k^4)+13*(6*k)*(20*k^3)*(15*k^4)-52*(15*k^4)^2+92*(6*k)^3*(6*k^5)+183*(6*k)*(15*k^2)*(6*k^5)-49*(20*k^3)*(6*k^5)+4*(6*k)*(15*k^2)^4+44*(6*k)^2*(15*k^2)^2*(20*k^3)+12*(15*k^2)^3*(20*k^3)+18*(6*k)^3*(20*k^3)^2+47*(6*k)*(15*k^2)*(20*k^3)^2-9*(20*k^3)^3+50*(6*k)^3*(15*k^2)*(15*k^4)+99*(6*k)*(15*k^2)^2*(15*k^4)+58*(6*k)^2*(20*k^3)*(15*k^4)-92*(6*k)*(15*k^4)^2+24*(6*k)^4*(6*k^5)+202*(6*k)^2*(15*k^2)*(6*k^5)+79*(15*k^2)^2*(6*k^5)-30*(6*k)*(20*k^3)*(6*k^5)-268*(15*k^4)*(6*k^5)+16*(6*k)*(15*k^2)^3*(20*k^3)+38*(6*k)^2*(15*k^2)*(20*k^3)^2+4*(15*k^2)^2*(20*k^3)^2-2*(6*k)*(20*k^3)^3+54*(6*k)^2*(15*k^2)^2*(15*k^4)+20*(15*k^2)^3*(15*k^4)+32*(6*k)^3*(20*k^3)*(15*k^4)+85*(6*k)*(15*k^2)*(20*k^3)*(15*k^4)-49*(20*k^3)^2*(15*k^4)-41*(6*k)^2*(15*k^4)^2-48*(15*k^2)*(15*k^4)^2+72*(6*k)^3*(15*k^2)*(6*k^5)+153*(6*k)*(15*k^2)^2*(6*k^5)+40*(6*k)^2*(20*k^3)*(6*k^5)+61*(15*k^2)*(20*k^3)*(6*k^5)-502*(6*k)*(15*k^4)*(6*k^5)-353*(6*k^5)^2+20*(6*k)*(15*k^2)^2*(20*k^3)^2+8*(6*k)^2*(20*k^3)^3-12*(15*k^2)*(20*k^3)^3+20*(6*k)*(15*k^2)^3*(15*k^4)+74*(6*k)^2*(15*k^2)*(20*k^3)*(15*k^4)+24*(15*k^2)^2*(20*k^3)*(15*k^4)-26*(6*k)*(20*k^3)^2*(15*k^4)-2*(6*k)^3*(15*k^4)^2-16*(6*k)*(15*k^2)*(15*k^4)^2-96*(20*k^3)*(15*k^4)^2+78*(6*k)^2*(15*k^2)^2*(6*k^5)+28*(15*k^2)^3*(6*k^5)+32*(6*k)^3*(20*k^3)*(6*k^5)+138*(6*k)*(15*k^2)*(20*k^3)*(6*k^5)+24*(20*k^3)^2*(6*k^5)-316*(6*k)^2*(15*k^4)*(6*k^5)-112*(15*k^2)*(15*k^4)*(6*k^5)-706*(6*k)*(6*k^5)^2+8*(6*k)*(15*k^2)*(20*k^3)^3-8*(20*k^3)^4+44*(6*k)*(15*k^2)^2*(20*k^3)*(15*k^4)+16*(6*k)^2*(20*k^3)^2*(15*k^4)-20*(15*k^2)*(20*k^3)^2*(15*k^4)+12*(6*k)^2*(15*k^2)*(15*k^4)^2+16*(15*k^2)^2*(15*k^4)^2-80*(6*k)*(20*k^3)*(15*k^4)^2-64*(15*k^4)^3+28*(6*k)*(15*k^2)^3*(6*k^5)+96*(6*k)^2*(15*k^2)*(20*k^3)*(6*k^5)+28*(15*k^2)^2*(20*k^3)*(6*k^5)+32*(6*k)*(20*k^3)^2*(6*k^5)-64*(6*k)^3*(15*k^4)*(6*k^5)-136*(6*k)*(15*k^2)*(15*k^4)*(6*k^5)+16*(20*k^3)*(15*k^4)*(6*k^5)-512*(6*k)^2*(6*k^5)^2-132*(15*k^2)*(6*k^5)^2+24*(6*k)*(15*k^2)*(20*k^3)^2*(15*k^4)-24*(20*k^3)^3*(15*k^4)+16*(6*k)*(15*k^2)^2*(15*k^4)^2-8*(6*k)^2*(20*k^3)*(15*k^4)^2-64*(6*k)*(15*k^4)^3+56*(6*k)*(15*k^2)^2*(20*k^3)*(6*k^5)+32*(6*k)^2*(20*k^3)^2*(6*k^5)-24*(15*k^2)*(20*k^3)^2*(6*k^5)-32*(6*k)^2*(15*k^2)*(15*k^4)*(6*k^5)+16*(15*k^2)^2*(15*k^4)*(6*k^5)-16*(6*k)*(20*k^3)*(15*k^4)*(6*k^5)-64*(15*k^4)^2*(6*k^5)-128*(6*k)^3*(6*k^5)^2-288*(6*k)*(15*k^2)*(6*k^5)^2+216*(20*k^3)*(6*k^5)^2+16*(6*k)*(15*k^2)*(20*k^3)*(15*k^4)^2-16*(20*k^3)^2*(15*k^4)^2-16*(6*k)^2*(15*k^4)^3+32*(6*k)*(15*k^2)*(20*k^3)^2*(6*k^5)-32*(20*k^3)^3*(6*k^5)+16*(6*k)*(15*k^2)^2*(15*k^4)*(6*k^5)+16*(15*k^2)*(20*k^3)*(15*k^4)*(6*k^5)-96*(6*k)*(15*k^4)^2*(6*k^5)-128*(6*k)^2*(15*k^2)*(6*k^5)^2-32*(15*k^2)^2*(6*k^5)^2+128*(6*k)*(20*k^3)*(6*k^5)^2+112*(15*k^4)*(6*k^5)^2+32*(6*k)*(15*k^2)*(20*k^3)*(15*k^4)*(6*k^5)-32*(20*k^3)^2*(15*k^4)*(6*k^5)-32*(6*k)^2*(15*k^4)^2*(6*k^5)-32*(6*k)*(15*k^2)^2*(6*k^5)^2+32*(15*k^2)*(20*k^3)*(6*k^5)^2+64*(6*k)*(15*k^4)*(6*k^5)^2-32*(6*k^5)^3

Then we use the formula for the Chern class of a tensor product of vector bundles, and we get the numerator of $c(\mathcal{E})$ in $e$.

In [42]:
cE_e_num=0
sym_bundle_pol=Le(sym_bundle)
rank_sym=binomial(2+n-1,2)
for deg in range(rank_sym+1):
    tensor_deg=0
    for k_exp in range(n+1):
        for r_exp in range(2*n):
            if (k_exp+r_exp)==deg:
                tensor_deg=tensor_deg+sym_bundle_pol.coefficient([k_exp,r_exp])*k^(k_exp)*r^(r_exp)*(1-2*r)**(rank_sym-deg)
    cE_e_num=cE_e_num+tensor_deg
print(cE_e_num)

-4*r^5 + 100*k*r^3 - 48*r^4 - 250*k^2*r + 220*k*r^2 - 55*r^3 + 110*k^2 - 160*k*r + 60*r^2 + 16*k - 12*r + 1


Now we compute the Chern class of the denominator

In [43]:
cE_e_den=0
cTP=(1+k)**(n+1)
cTP_pol=Le(cTP)
rank_cTP=n
for deg in range(rank_cTP+1):
    tensor_deg=0
    for k_exp in range(n+1):
        for r_exp in range(2*n):
            if (k_exp+r_exp)==deg:
                tensor_deg=tensor_deg+cTP_pol.coefficient([k_exp,r_exp])*k^(k_exp)*r^(r_exp)*(1-r)**(rank_cTP-deg)
    cE_e_den=cE_e_den+tensor_deg
print(cE_e_den)

6*k^2 - 8*k*r + 3*r^2 + 4*k - 3*r + 1


This is the Chern class of $c(\mathcal{E}|_e)$. This is a bundle of rank $3$, it must have only three Chern classes.

In [44]:
sE_e_den=1
cE_e_den_pol=Le(cE_e_den)
deg_cE_e_den=cE_e_den_pol.degree(std_grading=True)
for deg in range(dimB3-1):
    product=sE_e_den*cE_e_den
    product_pol=Le(product)
    s_deg=0
    for k_exp in range(n+1):
        for r_exp in range(2*n):
            if (k_exp+r_exp)==deg+1:
                s_deg=s_deg+product_pol.coefficient([k_exp,r_exp])*k^(k_exp)*r^(r_exp)
    sE_e_den=sE_e_den-s_deg
print(sE_e_den)

10*k*r^3 - 6*r^4 + 20*k^2*r - 20*k*r^2 + 5*r^3 + 10*k^2 - 16*k*r + 6*r^2 - 4*k + 3*r + 1


In [45]:
cE_e=cE_e_num*sE_e_den
print(cE_e)

-56*k^2*r + 48*k*r^2 - 12*r^3 + 56*k^2 - 80*k*r + 30*r^2 + 12*k - 9*r + 1


Now we want to construct the full Chern class of the bundle, combining this Chern class with the one outside of $e$

In [46]:
cE_open

-20*l^3*m^2 - 20*l^2*m^3 + 20*l^3*m + 20*l^2*m^2 + 20*l*m^3 + 20*l^3 + 40*l^2*m + 40*l*m^2 + 20*m^3 + 15*l^2 + 26*l*m + 15*m^2 + 6*l + 6*m + 1

In [47]:
cE_e_pol=Le(cE_e)
cE=1
for m_exp in range(n+1):
    for e_exp in range(2*n+1):
        if e_exp!=0:
            if m_exp+e_exp<=binomial(2+n-1,2)-n:
            #if m_exp+e_exp<=n:
                temp=cE_e_pol.coefficient([m_exp,e_exp])
                cE=cE+temp.constant_coefficient()*m^(m_exp)*e^(e_exp)
print("Pay attention! You want the n-th part to have integer coefficients")

diag=0
for i in range(n+1):
    diag=diag+l^i*m^(n-i)

cE_open_pol=L3(cE_open)
for deg in range(binomial(2+n-1,2)-n):
#for deg in range(n):
    s_deg=0
    const_deg=0
    for m_exp in range(n+1):
        for l_exp in range(n+1):
            if (m_exp+l_exp)==deg+1:
                    s_deg=s_deg+cE_open_pol.coefficient([l_exp,m_exp,0])*m^(m_exp)*l^(l_exp)
                    const_deg=const_deg+cE_open_pol.coefficient([l_exp,m_exp,0])
    if deg+1>=n:    
        cE=cE+s_deg-((const_deg)/(n+1))*diag*m^(deg+1-n)
    else:
        cE=cE+s_deg
print(cE)

Pay attention! You want the n-th part to have integer coefficients
-10*l^3 + 10*l^2*m + 10*l*m^2 - 10*m^3 - 56*m^2*e + 48*m*e^2 - 12*e^3 + 15*l^2 + 26*l*m + 15*m^2 - 80*m*e + 30*e^2 + 6*l + 6*m - 9*e + 1


Here are the lines that verify what is stated in Remark 4.15. The variable ```amb``` adds factors of type $m^j[\Delta]$.

In [ ]:
amb=0
for j in range(n):
    amb=amb+(-1)**(j+1)*e**(j+1)*m**(n-j-1)*binomial(n+1,n-j-1)

if conjecture: 
    for j in range(n):
        cE=cE+n^15*m^(j+1)*amb

Here we compute the Segre class $s(\mathcal{E})$. 

In [48]:
sE=1
cE_pol=L3(cE)
deg_cE=cE_pol.degree(std_grading=True)
for deg in range(dimB3):
    product=sE*(cE)
    product_pol=L3(product)
    s_deg=0
    for m_exp in range(n+1):
        for l_exp in range(n+1):
            for e_exp in range(2*n+1):
                if (m_exp+l_exp+e_exp)==deg+1:
                    s_deg=s_deg+product_pol.coefficient([l_exp,m_exp,e_exp])*m^(m_exp)*l^(l_exp)*e^(e_exp)
    sE=sE-s_deg
print(sE)
sE_pol=L3(sE)
sE*cE == 1

-68404*l^3*m^3 + 1440896*m^3*e^3 - 738888*m^2*e^4 + 212904*m*e^5 - 26613*e^6 + 5524*l^3*m^2 + 5524*l^2*m^3 + 69056*m^3*e^2 - 39384*m^2*e^3 + 12900*m*e^4 - 1935*e^5 - 84*l^3*m + 286*l^2*m^2 - 84*l*m^3 - 1664*m^3*e + 3496*m^2*e^2 - 2064*m*e^3 + 387*e^4 - 26*l^3 - 166*l^2*m - 166*l*m^2 - 26*m^3 + 1016*m^2*e - 804*m*e^2 + 201*e^3 + 21*l^2 + 46*l*m + 21*m^2 - 136*m*e + 51*e^2 - 6*l - 6*m + 9*e + 1


True

In [49]:
#Here we store the coefficients where e appears at least once. Ignore the first column
mat_e = matrix(QQ,n+1,2*n+1)
for u in range(n+1):
    for v in range(2*n+1):
        if v!=0: 
            mat_e[u,v]=sE_pol.coefficient([0,u,v])
print(mat_e)

#Here we store the coefficients where e does not appear

mat_not_e = matrix(n+1,n+1)
for u in range(n+1):
    for v in range(n+1):
        mat_not_e[u,v]=sE_pol.coefficient([u,v,0])
print(mat_not_e)


[      0       9      51     201     387   -1935  -26613]
[      0    -136    -804   -2064   12900  212904       0]
[      0    1016    3496  -39384 -738888       0       0]
[      0   -1664   69056 1440896       0       0       0]
[     1     -6     21    -26]
[    -6     46   -166    -84]
[    21   -166    286   5524]
[   -26    -84   5524 -68404]


In [50]:
#Now we get the intersection numbers involving z where e appears at least once
#Here we store the coefficients where e appears at least once
i4_e = matrix(QQ,n+1,2*n+1) #Ignore the first column
for u in range(n+1):
    for v in range(2*n+1):
        if v!=0:
            for a in range(n+1):
                for b in range(n+1):
                    for c in range(dimB3+1):
                        if u+v+a+b+c==dimB3: 
                            if c!=0:
                                if a==0: #We don't want l^a*m^b*e^c but only m^{b}*e^c
                                    if b+u<=n:
                                        i4_e[u,v]=i4_e[u,v]+mat_e[b,c]*i3[0,b+u]*(-1)**(dimB4-u-v)
                            if c==0:
                                if a+b+u<=n:
                                    i4_e[u,v]=i4_e[u,v]+mat_not_e[a,b]*i3[0,a+b+u]*(-1)**(dimB4-u-v)

print(i4_e)

[    0 -1820  -580   340    12   -60    20]
[    0  -890   190    54   -42    10     0]
[    0     0    68   -24     4     0     0]
[    0    51    -9     1     0     0     0]


These comments concerns the case $n=2$. 

The $(0,1)$-entry of the matrix gives the intersection number for $ez^3=e(3l+3m-4e)^3=8e^4=-6\cdot8$, which is the result we expect from Aluffi.

The $(1,1)$-entry of the matrix gives the intersection number for $mez^2=em(3l+3m-4e)^2=-48m^2e^2 + 16me^3=-48\cdot(-1)+16\cdot(-3)=0$, which is the result we expect from Aluffi [Alu90].

In [51]:
#Now we get the intersection numbers involving z where e does not appear
#Here we store the coefficients where e appears at least once
i4_not_e = matrix(QQ,n+1,n+1) #Ignore the first column
for u in range(n+1):
    for v in range(n+1):
        for a in range(n+1):
                for b in range(n+1):
                    for c in range(dimB3+1):
                        if u+v+a+b+c==dimB3: 
                            if c!=0:
                                if a==0: #We don't want l^a*m^b*e^c but only m^{a+b}*e^c
                                    if b+u+v<=n:
                                        i4_not_e[u,v]=i4_not_e[u,v]+mat_e[b,c]*i3[0,b+u+v]*(-1)**(dimB4-u-v)
                            if c==0:
                                if a+u<=n:
                                    if b+v<=n:
                                        i4_not_e[u,v]=i4_not_e[u,v]+mat_not_e[a,b]*(-1)**(dimB4-u-v)

print(i4_not_e)

[13720  1610  -600  -175]
[ 1610  -230   -35    21]
[ -600   -35    46     6]
[ -175    21     6     1]


These comments concerns the case $n=2$. 

The $(0,0)$-entry of the matrix gives the intersection number for $z^4=(3l+3m-4e)^4=486l^2m^2 + 3456m^2e^2 - 1536me^3 + 256e^4=486 - 3456 +3\cdot 1536 - 256\cdot6=102$, which is the result we expect from Aluffi.

The $(1,1)$-entry of the matrix gives the intersection number for $mlz^2=ml(3l+3m-4e)^2=18l^2m^2 + 16m^2e^2=-18\cdot+16\cdot(-1)=2$, which is the result we expect from Aluffi [Alu90].

Now we describe the Chow ring of $B_4$ ```CHB4```. In the following lines $z$ plays the role of $c_1(\mathcal{O}_{B_4}(-1))$. Then we just need to understand the intersection numbers involving $z$, using the usual strategy involving $s(N_{B_3}V_3)$.
We will do this only in the case $n=3$, where $\dim B_4=8$.

In [53]:
l,m,e,z = var('l, m, e, z')
E = QQ[l, m, e,z]
relations4 = []
relations4.append(m**(n+1))
relations4.append(l**(n+1))
relations4.append(e**(2*n+1))
relations4.append(z**(dimB4+1))
for u in range(n+1,2*n+1):
    for o in range(2*n+1-u,n+1):
        if u != 0:
            relations4.append((e**u)*(m**o))
for u in range(n+1):
    if u != 0:
        relations4.append(e*(m**u-l**u)) 
for u1 in range(n+1):
    for u2 in range(n+1):
        for u3 in range(2*n+1):
            if u != 0:
                if dimB4+1-u1-u2-u3>=0:
                    relations4.append(z**(dimB4+1-u1-u2-u3)*m**u1*l**u2*e**u3)
temp=0
for i in range(n+1):
    temp=temp+l^i*m^(n-i)
for j in range(n):
    temp=temp+(-1)**(j+1)*e**(j+1)*m**(n-j-1)*binomial(n+1,n-j-1)
relations4.append(temp)

#This is true only for n=3
#wl.append(-z**3+(6*l + 6*m - 9*e)*z**2-(15*l^2 + 26*l*m + 15*m^2 - 80*m*e + 30*e^2)*z-10*l^3 + 10*l^2*m + 10*l*m^2 - 10*m^3 - 56*m^2*e + 48*m*e^2 - 12*e^3)
I = E.ideal(relations4)
S.<l,m,e,z> = E.quotient(I)
L4=S.lifting_map()

# Computing the Chern class $c(N_{B_4} V_4)$

The Chern class $c(N_{B_4}V_4)$ is computed by using $c(N_{B_4}V_4)=c(N_{E_4}V_4) c(N_{B_4}E_4)=:c_1\cdot c_2$

In [54]:
c1=1+z

To compute $c_2$ recall that $N_{B_4}E_4 \simeq \pi_4^*(N_{B_3}V_3/\mathcal{E})\otimes \mathcal{O}_{B_4}(1)$- The rank of this bundle is $\dim(V_0)-1-\dim(B_4)$.

In [55]:
c2=0
quotient=cNB3V3*sE
quotient_pol=L4(quotient)
rank_quotient=C-Q
for deg in range(rank_quotient+1):
    tensor_deg=0
    for m_exp in range(n+1):
        for l_exp in range(n+1):
            for e_exp in range(2*n+1):
                for z_exp in range(dimB4+1):
                    if (m_exp+l_exp+e_exp+z_exp)==deg:
                        tensor_deg=tensor_deg+quotient_pol.coefficient([l_exp,m_exp,e_exp,z_exp])*m^(m_exp)*l^(l_exp)*e^(e_exp)*z^(z_exp)*(1-z)**(rank_quotient-deg)
    c2=c2+tensor_deg

For $n=3$, the rank of $N_{B_4}V_4$ is $19-8=11$. In general it is given by $\dim(V_0)-\dim(B_4)$.

In [56]:
cNB4V4=c1*c2

Here we compute the Segre class $s(N_{B_4}V_4)$

In [57]:
sNB4V4=1
cNB4V4_pol=L4(cNB4V4)
for deg in range(dimB4+1):
    product=sNB4V4*(cNB4V4)
    product_pol=L4(product)
    s_deg=0
    for m_exp in range(n+1):
        for l_exp in range(n+1):
            for e_exp in range(2*n+1):
                for z_exp in range(dimB4+1):
                    if (m_exp+l_exp+e_exp+z_exp)==deg+1:
                        s_deg=s_deg+product_pol.coefficient([l_exp,m_exp,e_exp,z_exp])*m^(m_exp)*l^(l_exp)*e^(e_exp)*z^(z_exp)
    sNB4V4=sNB4V4-s_deg
sNB4V4*cNB4V4 == 1

True

# Computing the correction term on $B_4$

In [58]:
corr4=zero_matrix(QQ,C,1)

for n_points in range(C):
    n_lines=C-1-n_points
    integral4=(l+2*m)**n_points*(1+4*l+8*m-6*e-z)**n_lines*sNB4V4
    integral4_pol=L4(integral4)
    deg5=integral4_pol.degree(std_grading=True)
    if deg5==dimB4 :
        for m_exp in range(n+1):
            for l_exp in range(n+1):
                for e_exp in range(2*n+1):
                    for z_exp in range(dimB4+1):
                        if (m_exp+l_exp+e_exp+z_exp)==deg5:
                            if e_exp==0:
                                corr4[n_points,0]=corr4[n_points,0]+integral4_pol.coefficient([l_exp,m_exp,e_exp,z_exp])*i4_not_e[l_exp,m_exp]
                            else:
                                corr4[n_points,0]=corr4[n_points,0]+integral4_pol.coefficient([l_exp,m_exp,e_exp,z_exp])*i4_e[m_exp,e_exp]

print(corr4)

[-460870176]
[ 142629112]
[  45754840]
[   7186504]
[    685584]
[     37920]
[      1120]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]
[         0]


# Characteristic numbers

In [59]:
start=zero_matrix(QQ,C,1)

for n_points in range(C):
    n_lines=C-1-n_points
    start[n_points]=4^(n_lines)
char_numbers=start-(corr0+corr1+corr2+corr3+corr4)
print(char_numbers)

[213642327616]
[ 61810371328]
[ 16615227040]
[  4266198896]
[  1072926016]
[   268391296]
[    67107584]
[    16777216]
[     4194304]
[     1048576]
[      262144]
[       65536]
[       16384]
[        4096]
[        1024]
[         256]
[          64]
[          16]
[           4]
[           1]
